In [9]:
import pandas
import os
import re
import json
from nltk.corpus import wordnet

In [10]:
# If table name is given directly check for matching columns only in those tables. No need
# to check context or ontologies if table name is mentioned in requirements.

def searchTable():
    op = open("Output_match.txt",'w')
    op.write("Format of output is : Table_Name    Column_Name    Data_Type\n")
    f=open("final_schema.txt",'r')
    for line in f.readlines():
        json_object=json.loads(line)
        table=json_object["tablename"]
        schema=json_object["schema"]
        if table in input_table:
            count=0
            for col,dtype in schema.items():
                if (col in input_schema) and (input_schema[col]==dtype):
                    count+=1
                    op.write(table+'\t\t\t'+col+'\t\t\t'+dtype+'\n')
            global total
            op.write(table+" match score "+str(count)+" of "+str(total)+"\n")

In [11]:
# Step 1: Retrieve all the tables with matching column names and also retrieve the table names of 
# ontologically matching columns.
# Step 2: Within this set of retrieved tables , check for contextually matching columns or by 
# asking for some context from the user , try returning the contextually correct tables.
# Step 3: If there are contextually matching tables , check for possible merges.


def searchAll(tables_list):
    f=open("final_schema.txt",'r')
    for line in f.readlines():
        json_object=json.loads(line)
        table=json_object["tablename"]
        schema=json_object["schema"]
        count=0
        for col,dtype in schema.items():
            if (col in input_schema) and (input_schema[col]==dtype):
                count+=1
                tables_list.add(table)
                for key , val in onto.items():
                    for col_name in onto[key]:
                        if (col_name in input_schema) and (input_schema[col_name]==dtype):
                            tables_list.add(table)
        global total
    f.close()
    return tables_list #Contains the list of all the possible output tables. Check for matching categories from this list.

In [12]:
def get_synonyms(word):
    meanings=set()
    for synset in wordnet.synsets(word,pos=wordnet.NOUN):
        for lemma in synset.lemmas():
            meanings.add(lemma.name())
    for synset in wordnet.synsets(word,pos=wordnet.NOUN):
        for hypernym in synset.hypernyms():
            meanings.add(hypernym.lemma_names()[0])
    meanings.add(word)
    return list(meanings)

In [13]:
def generate_ontology(input_schema):
    ontology={}
    for col in input_schema:
        ontology[col]=get_synonyms(col)
    return ontology

In [14]:
# This function parses the schema file to find the table and retrieve its' categories.
def find_categories(table):
    f=open("final_schema.txt",'r')
    for line in f.readlines():
        json_object=json.loads(line)
        json_table=json_object["tablename"]
        if(json_table == table):
            return json_object["categories"]

In [15]:
# Checks if the keys of the input context are present themselves , otherwise checks if their onctologies are present in the categories.
def check_context(table , tables_list , categories_onto , match_count):
    for table_name in tables_list:
        if(table == table_name): #Skip checking a table with itself , it will obviously match.
            continue
        else:
            cat = find_categories(table_name)
            for key , value in categories_onto.items():
                if (key in cat):# If the category names are directly present
                    match_count = match_count + 1
                    continue
                else:# Else check if ontologies of each categories match
                    for iterator in value:
                        if(iterator in cat):
                            match_count = match_count + 1
                            break
        print(" Context match of " + table + " with " + table_name + " is " + str(match_count) + " by " + str(len(categories_onto.keys())) + "\n")

In [16]:
with open("input.txt",'r') as input_file:
    match_count = 0
    tables_list = set()
    input_obj=json.load(input_file)
    input_schema = input_obj["schema"]
    onto = generate_ontology(input_schema) # To generate ontologies for the input columns. Returns a dictionary.
    
#     for key,val in onto.items(): # To print the ontology dictionary.
#         print(key , "->" , val)
    
    total=0
    for i in input_schema:
        total+=1
    if "tablename" in input_obj:
        input_table = input_obj["tablename"]
        searchTable()
        exit()
    else:
        table_list = searchAll(tables_list)
    
#     Now we have a list of possible output tables. Check for context now.
    for table in tables_list:
        categories_list = []
        categories_list = find_categories(table)
        print(categories_list)
        categories_onto = generate_ontology(categories_list) # Returns a dictionary of ontologies for each word.
        print(categories_onto)
        check_context(table , tables_list , categories_onto , match_count)

['rhone', 'resorts', 'municipalities', 'populated', 'ski', 'areas', 'switzerland', 'valais', 'places']
{'rhone': ['Rhone_River', 'Rhone', 'rhone'], 'resorts': ['repair', 'resort_hotel', 'hotel', 'resorts', 'aid', 'resource', 'refuge', 'hangout', 'stamping_ground', 'resort', 'area', 'haunt', 'holiday_resort', 'recourse'], 'municipalities': ['municipalities', 'gathering', 'urban_area', 'administrative_district', 'municipality'], 'populated': ['populated'], 'ski': ['ski', 'runner'], 'areas': ['arena', 'surface_area', 'topic', 'domain', 'sphere', 'expanse', 'body_part', 'areas', 'structure', 'field', 'area', 'region', 'environment', 'orbit', 'country', 'extent'], 'switzerland': ['Svizzera', 'Switzerland', 'switzerland', 'Suisse', 'Schweiz', 'Swiss_Confederation'], 'valais': ['valais'], 'places': ['seat', 'public_square', 'area', 'billet', 'topographic_point', 'space', 'geographical_area', 'post', 'berth', 'lieu', 'office', 'home', 'condition', 'position', 'point', 'passage', 'situation', '

 Context match of Fiesch with Diving at the 2011 World Aquatics Championships - Women's 1 metre springboard is 13 by 9

 Context match of Fiesch with 2012-13 Exeter City F.C. season is 13 by 9

 Context match of Fiesch with Swimming at the 1999 Pan American Games - Women's 400 metre freestyle is 13 by 9

 Context match of Fiesch with Brazil at the 2008 Summer Olympics is 13 by 9

 Context match of Fiesch with 2008-09 Egyptian Premier League is 13 by 9

 Context match of Fiesch with Jiangmen is 13 by 9

 Context match of Fiesch with Oklahoma's 3rd congressional district is 13 by 9

 Context match of Fiesch with Men's 200 metres world record progression is 13 by 9

 Context match of Fiesch with Chief of the National Guard Bureau is 13 by 9

 Context match of Fiesch with Boldklubben Frem is 13 by 9

 Context match of Fiesch with France at the 1932 Summer Olympics is 13 by 9

 Context match of Fiesch with House of Medici is 13 by 9

 Context match of Fiesch with List of Grade I listed buil

 Context match of Fiesch with 2008-09 Debreceni VSC season is 23 by 9

 Context match of Fiesch with Philadelphia Phillies all-time roster (D) is 23 by 9

 Context match of Fiesch with 2009 in Thai football is 23 by 9

 Context match of Fiesch with Order of St. Olav is 23 by 9

 Context match of Fiesch with List of preserved Hunslet narrow gauge locomotives is 23 by 9

 Context match of Fiesch with Hilbre One Design is 23 by 9

 Context match of Fiesch with 1992-93 Segunda Division is 23 by 9

 Context match of Fiesch with Swimming at the 1995 Pan American Games - Women's 400 metre individual medley is 23 by 9

 Context match of Fiesch with Watford F.C. is 23 by 9

 Context match of Fiesch with 2005 Asian Athletics Championships - Women's javelin throw is 23 by 9

 Context match of Fiesch with Public toilet is 23 by 9

 Context match of Fiesch with List of Brazilian footballers is 23 by 9

 Context match of Fiesch with List of correctional facilities in New Zealand is 23 by 9

 Context

 Context match of List of North American Soccer League coaches with 1949-50 Huddersfield Town F.C. season is 12 by 9

 Context match of List of North American Soccer League coaches with 2003-04 Rangers F.C. season is 14 by 9

 Context match of List of North American Soccer League coaches with Austrian Supercup is 18 by 9

 Context match of List of North American Soccer League coaches with Gilbert Plains (electoral district) is 18 by 9

 Context match of List of North American Soccer League coaches with 2005-06 FIS Ski Jumping World Cup is 18 by 9

 Context match of List of North American Soccer League coaches with German submarine U-502 is 18 by 9

 Context match of List of North American Soccer League coaches with 2009-10 Fresno State Bulldogs men's basketball team is 19 by 9

 Context match of List of North American Soccer League coaches with List of tallest buildings in Boise is 20 by 9

 Context match of List of North American Soccer League coaches with 1980-81 San Antonio Spurs se

 Context match of List of North American Soccer League coaches with Louisiana State Senate is 74 by 9

 Context match of List of North American Soccer League coaches with List of gay, lesbian or bisexual people: I-J is 75 by 9

 Context match of List of North American Soccer League coaches with List of Members of the Canadian House of Commons with military service (P) is 75 by 9

 Context match of List of North American Soccer League coaches with Assistant Secretary of the Navy is 75 by 9

 Context match of List of North American Soccer League coaches with Diving at the 2011 World Aquatics Championships - Women's 1 metre springboard is 75 by 9

 Context match of List of North American Soccer League coaches with 2012-13 Exeter City F.C. season is 78 by 9

 Context match of List of North American Soccer League coaches with Swimming at the 1999 Pan American Games - Women's 400 metre freestyle is 79 by 9

 Context match of List of North American Soccer League coaches with Brazil at the 200

...

 Context match of List of Washington, D.C., railroads with Athletics at the 2011 All-Africa Games - Women's 5000 metres is 11 by 8

 Context match of List of Washington, D.C., railroads with Camellia is 11 by 8

 Context match of List of Washington, D.C., railroads with New South Wales 90 class locomotive is 12 by 8

 Context match of List of Washington, D.C., railroads with 2006 European Athletics Championships - Men's high jump is 12 by 8

 Context match of List of Washington, D.C., railroads with Lieutenant Governor of Indiana is 13 by 8

 Context match of List of Washington, D.C., railroads with Swimming at the 2012 European Aquatics Championships - Women's 50 metre breaststroke is 13 by 8

 Context match of List of Washington, D.C., railroads with List of works by Eero Saarinen is 14 by 8

 Context match of List of Washington, D.C., railroads with Judges of the Permanent Court of International Justice is 14 by 8

 Context match of List of Washington, D.C., railroads with MTV Roadi

 Context match of List of Washington, D.C., railroads with List of Grade I listed buildings in Salisbury is 42 by 8

 Context match of List of Washington, D.C., railroads with Minister of Transport (Canada) is 42 by 8

 Context match of List of Washington, D.C., railroads with Primary schools in Hertsmere is 42 by 8

 Context match of List of Washington, D.C., railroads with Doncaster Rovers F.C. is 42 by 8

 Context match of List of Washington, D.C., railroads with List of districts of Maharashtra is 43 by 8

 Context match of List of Washington, D.C., railroads with List of people who have won Academy, Emmy, Grammy, and Tony Awards is 44 by 8

 Context match of List of Washington, D.C., railroads with J, K and N-class destroyer is 44 by 8

 Context match of List of Washington, D.C., railroads with List of lakes of Switzerland is 46 by 8

 Context match of List of Washington, D.C., railroads with Australia women's national wheelchair basketball team at the 2012 Summer Paralympics is 4

 Context match of List of Washington, D.C., railroads with Maryland's 5th congressional district is 89 by 8

 Context match of List of Washington, D.C., railroads with Le Tour de Filipinas is 89 by 8

 Context match of List of Washington, D.C., railroads with Swimming at the 2010 Commonwealth Games - Men's 200 metre backstroke is 90 by 8

 Context match of List of Washington, D.C., railroads with 2010-11 North Carolina Tar Heels men's basketball team is 90 by 8

 Context match of List of Washington, D.C., railroads with List of Melbourne Victory FC players is 91 by 8

 Context match of List of Washington, D.C., railroads with 2003 Asian Athletics Championships - Women's triple jump is 91 by 8

 Context match of List of Washington, D.C., railroads with 1983 NHL Entry Draft is 91 by 8

 Context match of List of Washington, D.C., railroads with 2008-09 Debreceni VSC season is 91 by 8

 Context match of List of Washington, D.C., railroads with Philadelphia Phillies all-time roster (D) is 9

 Context match of List of Washington, D.C., railroads with 2012 Puerto Rico Islanders season is 121 by 8

 Context match of List of Washington, D.C., railroads with Swimming at the 2008 Summer Paralympics - Women's 200 metre individual medley SM13 is 121 by 8

 Context match of List of Washington, D.C., railroads with List of mayors of Seattle is 124 by 8

 Context match of List of Washington, D.C., railroads with Sequence assembly is 124 by 8

 Context match of List of Washington, D.C., railroads with Guardian of Zion Award is 124 by 8

 Context match of List of Washington, D.C., railroads with List of most recent executions by jurisdiction is 126 by 8

 Context match of List of Washington, D.C., railroads with Roman Catholic Archdiocese of Hartford is 126 by 8

 Context match of List of Washington, D.C., railroads with Elvir Rahimic is 126 by 8

 Context match of List of Washington, D.C., railroads with The Greatest Canadian is 127 by 8

 Context match of List of Washington, D.C., ra

KeyboardInterrupt: 